# Van der Pol equation

We consider the following problem :

\begin{equation} 
\left\{ 
\begin{aligned} 
{\mathrm d}_t y_1 & = y_2\\ 
{\mathrm d}_t y_2 & = \varepsilon \, (1 - y_1^2) \, y_2  - y_1 \quad \text{avec } \varepsilon > 0
\end{aligned} 
\right. 
\end{equation}


In [1]:
import numpy as np

from scipy.integrate import solve_ivp

from bokeh.io import push_notebook, show, output_notebook
from bokeh.plotting import figure
from bokeh.layouts import column
from bokeh.models import PrintfTickFormatter

from ipywidgets import interact, IntSlider, Dropdown, FloatSlider, Text

from mylib.model import vanderpol_model
import mylib.integration as integration

output_notebook(hide_banner=True)


## Quasi-exact solution

The quasi-exact solution is obtained by using an explicit Runge-Kutta method of order 5 with stepsize control and fine tolerances due to Dormand and Prince.

In [13]:
def plot_quasi_exact_sol():
    
    vdpm = vanderpol_model(eps=1)
    fcn = vdpm.fcn  
    
    tini = 0. 
    tend = 100.
    
    yini = (-2,-3)
    #yini = (+2, -10)
    sol = solve_ivp(fcn, (tini, tend), yini, method="RK45", rtol=1.e-12, atol=1.e-12)

    fig_sol = figure( width=950, height=300, title="Solution")
    plt_y1 = fig_sol.line(sol.y[0], sol.y[1], legend="y1", line_width=2,color='Blue')    
    fig_sol.legend.location = "top_left"
    a,b=sol.y[0].copy(), sol.y[1].copy()
    
    for i in range(len(a)):
        if(a[i]>1.5 and a[i]>a[i+1]):
            break;
    print(a[i],b[i])

    for j in range(i, len(a)):
        a[j]=a[i]
        b[j]=-3
    a[-1]=yini[0]
    b[-1]=yini[1]

    fig_sol.line(a, b, line_width=2,color='Red')  
    fig_sol.x(a[i-1],b[i-1],line_width=10 ,color='Black')
    fig_sol.x(a[i],b[i],line_width=10 ,color='Green')
    fig_sol.x(yini[0],yini[1],line_width=10 ,color='Blue')
    show(fig_sol, notebook_handle=True)
    
    '''
    def update(eps) :
        vdpm = vanderpol_model(eps)
        fcn = vdpm.fcn  
        sol = solve_ivp(fcn, (tini, tend), yini, method="RK45", rtol=1.e-12, atol=1.e-12)
        plt_y1.data_source.data = dict(x=sol.t, y=sol.y[0])
        push_notebook()
        
    interact(update, eps=FloatSlider(min=1.,max=20.,step=1., value=1., continuous_update=False))
'''
    
plot_quasi_exact_sol()

2.0130626937250686 0.0003413231279677364


## Characterization of stiffness

In [3]:
def plot_eigen_values():

    vdpm = vanderpol_model(eps=1)
    fcn = vdpm.fcn  
    jac = vdpm.jac

    tini = 0. 
    tend = 100.
    
    yini = (0.5, 0)
    
    sol = solve_ivp(fcn, (tini, tend), yini, method="RK45", rtol=1.e-12, atol=1.e-12)
    
    eig_vals = np.zeros((sol.t.size, 2), dtype=np.complex_)
    for it in range(0,sol.t.size):
        eig_vals[it], _ = np.linalg.eig(jac(0., sol.y[:,it]))

    lambda1 = eig_vals[:, 0]
    lambda2 = eig_vals[:, 1]

    fig_real = figure(x_range=(tini, tend), plot_height=300, plot_width=900, 
                      title = "Real part of eigenvalues (click on legend entries to hide corresponding plot)")
    fig_imag = figure(x_range=(tini, tend), plot_height=300, plot_width=900, 
                      title = "Imaginary part of eigenvalues (click on legend entries to hide corresponding plot)")
    
    plt_real1 = fig_real.line(sol.t, np.real(lambda1), legend="lambda1")
    plt_real2 = fig_real.line(sol.t, np.real(lambda2), color="Green", legend="lambda2")

    plt_imag1 = fig_imag.line(sol.t, np.imag(lambda1), legend="lambda1")
    plt_imag2 = fig_imag.line(sol.t, np.imag(lambda2), color="Green", legend="lambda2")
    
    fig_real.legend.click_policy="hide"
    fig_imag.legend.click_policy="hide"

    show(column(fig_real, fig_imag), notebook_handle=True)
        
    def update(eps):
                
        vdpm = vanderpol_model(eps)
        fcn = vdpm.fcn
        jac = vdpm.jac
                
        sol = solve_ivp(fcn, (tini, tend), yini, method="RK45", rtol=1.e-12, atol=1.e-12)

        eig_vals = np.zeros((sol.t.size, 2), dtype=np.complex_)
        for it in range(0,sol.t.size):
            eig_vals[it], _ = np.linalg.eig(jac(0., sol.y[:,it]))

        lambda1 = eig_vals[:, 0]
        lambda2 = eig_vals[:, 1]
        
        plt_real1.data_source.data = dict(x=sol.t, y=np.real(lambda1))
        plt_real2.data_source.data = dict(x=sol.t, y=np.real(lambda2))
        plt_imag1.data_source.data = dict(x=sol.t, y=np.imag(lambda1))
        plt_imag2.data_source.data = dict(x=sol.t, y=np.imag(lambda2))
        
        push_notebook()
 

    interact(update, eps=FloatSlider(min=1.,max=20.,step=1., value=1., continuous_update=False))

plot_eigen_values()

interactive(children=(FloatSlider(value=1.0, continuous_update=False, description='eps', max=20.0, min=1.0, st…

In [4]:
50000/1451

34.45899379738112

## Dormand and Price method

### Method of order 5

To compute global error, the quasi-exact solution is obtained by using an explicit Runge-Kutta method of order 8 with stepsize control and fine tolerances due to Dormand and Prince.

In [5]:
def plot_dopri5_sol():
    
    vdpm = vanderpol_model(eps=10)
    fcn = vdpm.fcn  
    jac = vdpm.jac

    tini = 0. 
    tend = 100.
    
    yini = (0.5, 0)
    
    fig_sol = figure(x_range=(tini, tend),  plot_height=300, plot_width=900, title="Solution")
    fig_err = figure(x_range=(tini, tend), y_axis_type="log", plot_height=300, plot_width=900, title="Global error")
    fig_dt = figure(x_range=(tini, tend), plot_height=300, plot_width=900, title="Time step")
    fig_err.yaxis[0].formatter = PrintfTickFormatter(format="%8.1e")

    tol = 1.e-4
    sol_dopri5 = solve_ivp(fcn, (tini, tend), yini, method="RK45", rtol=tol, atol=tol)
    y_exa = integration.quasi_exact(fcn, yini, sol_dopri5.t)
    y1_err = np.abs(y_exa[:, 0] - sol_dopri5.y[0])

    plt_sol_x_y1 = fig_sol.x(sol_dopri5.t, sol_dopri5.y[0], legend="y1", line_width=2)
    plt_sol_l_y1 = fig_sol.line(sol_dopri5.t, sol_dopri5.y[0], legend="y1")    
    fig_sol.legend.location = "top_left"
    
    plt_err_y1 = fig_err.x(sol_dopri5.t, y1_err, line_width=2, legend="y1")
    fig_err.legend.location = "bottom_left"
    
    dt = sol_dopri5.t[1::] - sol_dopri5.t[0:-1]
    plt_dt = fig_dt.x(sol_dopri5.t[0:-1], dt, line_width=2, legend="dt")
    
    show(column(fig_sol, fig_err, fig_dt), notebook_handle=True)
        
    def update(eps, tol):
        
        vdpm = vanderpol_model(eps)
        fcn = vdpm.fcn
        jac = vdpm.jac

        sol_dopri5 = solve_ivp(fcn, (tini, tend), yini, rtol=tol, atol=tol)
        y_exa = integration.quasi_exact(fcn, yini, sol_dopri5.t)
        y1_err = np.abs(y_exa[:, 0] - sol_dopri5.y[0])
        dt = sol_dopri5.t[1::] - sol_dopri5.t[0:-1]
        
        plt_sol_x_y1.data_source.data = dict(x=sol_dopri5.t, y=sol_dopri5.y[0])
        plt_sol_l_y1.data_source.data = dict(x=sol_dopri5.t, y=sol_dopri5.y[0])
        plt_err_y1.data_source.data = dict(x=sol_dopri5.t, y=y1_err)
        plt_dt.data_source.data = dict(x=sol_dopri5.t[0:-1], y=dt)
        
        print("   Number of time step : " + str(sol_dopri5.t.size))

        push_notebook()
              
    dtol={'1.e-2':1.e-2, '1.e-4':1.e-4, '1.e-6':1.e-6, '1.e-8':1.e-8, '1.e-10':1.e-10}     
    interact(update, eps=FloatSlider(min=1.,max=20.,step=1., value=1., continuous_update=False), 
             tol=Dropdown(options=dtol, value=1.e-4, description='tol'))

plot_dopri5_sol()

interactive(children=(FloatSlider(value=1.0, continuous_update=False, description='eps', max=20.0, min=1.0, st…

### RK4 fixed step

In [6]:
def plot_rk4():
    
    vdpm = vanderpol_model(eps=20)
    fcn = vdpm.fcn  
    jac = vdpm.jac

    tini = 0. 
    tend = 100.
    
    yini = (0.5, 0)
    
    fig_sol = figure(x_range=(tini, tend),  plot_height=300, plot_width=900, title="Solution")
    fig_err = figure(x_range=(tini, tend), y_axis_type="log", plot_height=300, plot_width=900, title="Global error")
    fig_dt = figure(x_range=(tini, tend), plot_height=300, plot_width=900, title="Time step")
    fig_err.yaxis[0].formatter = PrintfTickFormatter(format="%8.1e")
    
    nt=50000
    tol = 1.e-4
    sol_rk = integration.rk4(tini, tend, nt, yini, fcn) 
    y_exa = integration.quasi_exact(fcn, yini, sol_rk.t)
    y1_err = np.abs(y_exa[:, 0] - sol_rk.y[0])

    plt_sol_x_y1 = fig_sol.x(sol_rk.t, sol_rk.y[0], legend="y1", line_width=2)
    plt_sol_l_y1 = fig_sol.line(sol_rk.t, sol_rk.y[0], legend="y1")    
    fig_sol.legend.location = "top_left"
    
    plt_err_y1 = fig_err.x(sol_rk.t, y1_err, line_width=2, legend="y1")
    fig_err.legend.location = "bottom_left"
    
    show(column(fig_sol, fig_err, fig_dt), notebook_handle=True)

plot_rk4()

### Method of order 8

To compute global error, the quasi-exact solution is obtained by using an explicit Runge-Kutta method of order 8 with stepsize control and fine tolerances due to Dormand and Prince.

In [3]:
def plot_dopri853_sol():
    
    vdpm = vanderpol_model(eps=10)
    fcn = vdpm.fcn  
    jac = vdpm.jac

    tini = 0. 
    tend = 100.
    
    yini = (0.5, 0)
    
    fig_sol = figure(x_range=(tini, tend),  plot_height=300, plot_width=900, title="Solution")
    fig_err = figure(x_range=(tini, tend), y_axis_type="log", plot_height=300, plot_width=900, title="Global error")
    fig_dt = figure(x_range=(tini, tend), plot_height=300, plot_width=900, title="Time step")

    tol = 1.e-4
    t_dopri853, y_dopri853 = integration.dopri853(tini, tend, yini, fcn, tol)
    y_exa = integration.quasi_exact(fcn, yini, t_dopri853)
    y1_err = np.abs(y_exa[:, 0] - y_dopri853[:,0])

    plt_sol_x_y1 = fig_sol.x(t_dopri853, y_dopri853[:, 0], legend="y1", line_width=2)
    plt_sol_l_y1 = fig_sol.line(t_dopri853, y_dopri853[:, 0], legend="y1")
    fig_sol.legend.location = "top_left"
    
    plt_err_y1 = fig_err.x(t_dopri853, y1_err, line_width=2, legend="y1")
    fig_err.legend.location = "bottom_left"
    
    dt = t_dopri853[1::] - t_dopri853[0:-1]
    plt_dt = fig_dt.x(t_dopri853[0:-1], dt, line_width=2, legend="dt")
    
    show(column(fig_sol, fig_err, fig_dt), notebook_handle=True)
    
    def update(eps, tol):
        
        vdpm = vanderpol_model(eps)
        fcn = vdpm.fcn
        jac = vdpm.jac

        t_dopri853, y_dopri853 = integration.dopri853(tini, tend, yini, fcn, tol)
        y_exa = integration.quasi_exact(fcn, yini, t_dopri853)
        y1_err = np.abs(y_exa[:, 0] - y_dopri853[:,0])
        dt = t_dopri853[1::] - t_dopri853[0:-1]

        plt_sol_x_y1.data_source.data = dict(x=t_dopri853, y=y_dopri853[:,0])
        plt_sol_l_y1.data_source.data = dict(x=t_dopri853, y=y_dopri853[:,0])
        plt_err_y1.data_source.data = dict(x=t_dopri853, y=y1_err)
        plt_dt.data_source.data = dict(x=t_dopri853[0:-1], y=dt)
        
        print("   Number of time step : " + str(t_dopri853.size))

        push_notebook()
        
    dtol={'1.e-2':1.e-2, '1.e-4':1.e-4, '1.e-6':1.e-6, '1.e-8':1.e-8, '1.e-10':1.e-10}     
    interact(update, eps=FloatSlider(min=1.,max=20.,step=1., value=1., continuous_update=False), 
             tol=Dropdown(options=dtol, value=1.e-4, description='tol'))
    
plot_dopri853_sol()

interactive(children=(FloatSlider(value=1.0, continuous_update=False, description='eps', max=20.0, min=1.0, st…

### time steps vs tolerance

In [44]:
import warnings
warnings.filterwarnings('ignore')

def plot_embedded_cost():

    tini = 0. 
    tend = 100.
    
    yini = (0.5, 0)
    
    bm = vanderpol_model(eps=20)
    fcn = bm.fcn
            
    l_nt = [101, 501, 1001, 5001, 10001, 20001]
    

    fe_rk4=[]
    norm_rk4=[]
    for nt in l_nt:
        sol_exa = solve_ivp(fcn, (tini, tend), yini, rtol=1.e-12, atol=1.e-12, t_eval=np.linspace(tini, tend, nt))
        sol_yrk4 = integration.rk4(tini, tend, nt, yini, fcn)
        #fe_rk4.append(sol_yrk4.nfev)
        fe_rk4.append(sol_yrk4.t.size-1)
        norm_rk4.append(np.linalg.norm(sol_exa.y-sol_yrk4.y) / np.sqrt(nt))
     
    l_tol = [1.e-2, 1.e-4, 1.e-6, 1.e-8,1.e-10, 1.e-11]
    fe_dopri853=[]
    norm_dopri853=[]

    fe_dopri=[]
    norm_dopri=[]

    
    sol_rk4 = integration.rk4(tini, tend, nt, yini, fcn)

    for tol in l_tol:
        sol_dopri853 =integration.dopri853(tini, tend, yini, fcn, tol)
        sol = solve_ivp(fcn, (tini, tend), yini, rtol=1.e-13, atol=1.e-13, t_eval=sol_dopri853[0])
        #sol_rk_emb.t.size-1
        #fe_dopri.append(sol_dopri.nfev)
        fe_dopri853.append(sol_dopri853[0].size-1)
        err = 0 
        #return sol_dopri
        for i in range(sol_dopri853[0].size):
            ldt = sol_dopri853[0][i]
            err += ldt * ((sol.y[0,i]-sol_dopri853[1].T[0,i])*(sol.y[0,i]-sol_dopri853[1].T[0,i]) + \
                           (sol.y[1,i]-sol_dopri853[1].T[1,i])*(sol.y[1,i]-sol_dopri853[1].T[1,i])  )
        err = np.sqrt(err)    
        norm_dopri853.append(err)
    
    
    for tol in l_tol:
        sol_dopri =solve_ivp(fcn, (tini, tend), yini, method="RK45", rtol=tol, atol=tol)
        sol = solve_ivp(fcn, (tini, tend), yini, rtol=1.e-13, atol=1.e-13, t_eval=sol_dopri.t)
        #sol_rk_emb.t.size-1
        #fe_dopri.append(sol_dopri.nfev)
        fe_dopri.append(sol_dopri.t.size-1)
        err = 0 
        #return sol_dopri
        for i in range(sol_dopri.t.size):
            ldt = sol_dopri.t[i]
            err += ldt * ((sol.y[0,i]-sol_dopri.y[0,i])*(sol.y[0,i]-sol_dopri.y[0,i]) + \
                           (sol.y[1,i]-sol_dopri.y[1,i])*(sol.y[1,i]-sol_dopri.y[1,i])  )
        err = np.sqrt(err)    
        norm_dopri.append(err)
    #fig = figure(x_axis_type="log", y_axis_type="log", plot_height=500, plot_width=900, title= "Number of function evaluations vs norm of global error"
    #           )
    #fig = figure(x_axis_type="log", y_axis_type="log", plot_height=500, plot_width=900, title= "Number of time steps vs norm of global error" )
    #fig.x(norm_dopri, fe_dopri, legend="DOPRI", color="Indigo")
    #fig.line(norm_dopri, fe_dopri, legend="DOPRI", color="Indigo")
    #fig.x(norm_rk_emb, fe_rk_emb, legend="rk embedded", color="Green")
    #fig.line(norm_rk_emb, fe_rk_emb, legend="rk embedded", color="Green")
    fig = figure(x_axis_type="log", y_axis_type="log", plot_height=500, plot_width=900,
                 title= "accepted time steps vs tolerance")
    fig.x(l_tol, fe_dopri, legend="DOPRI", color="Indigo")
    fig.line(l_tol, fe_dopri, legend="DOPRI", color="Indigo")
    fig.x(l_tol, fe_dopri853, legend="DOPRI853", color="red")
    fig.line(l_tol, fe_dopri853, legend="DOPRI853", color="red")
    #fig.x(l_tol, fe_dopri853, legend="DOPRI853", color="red")
    #fig.line(l_tol, fe_dopri853, legend="DOPRI853", color="red")
    fig.legend.location = "top_right"
    show(fig)
    
a=plot_embedded_cost()

### time steps vs epsilon

In [49]:
import warnings
warnings.filterwarnings('ignore')

def plot_embedded_cost():

    tini = 0. 
    tend = 100.
    
    yini = (0.5, 0)
    
    
            
    l_nt = [101, 501, 1001, 5001, 10001, 20001]
    l_eps= [1,2,4,6,8,10,12,14,16,17,18,19,20]
     
    l_tol = [1.e-2, 1.e-4, 1.e-6, 1.e-8,1.e-10, 1.e-11]
    tol=l_tol[-2]
    
    fe_dopri853=[]
    norm_dopri853=[]

    fe_dopri=[]
    norm_dopri=[]

    

    for eps in l_eps:
        vm= vanderpol_model(eps=eps)
        fcn = vm.fcn
        sol_dopri853 =integration.dopri853(tini, tend, yini, fcn, tol)
        sol = solve_ivp(fcn, (tini, tend), yini, rtol=1.e-13, atol=1.e-13, t_eval=sol_dopri853[0])
        #sol_rk_emb.t.size-1
        #fe_dopri.append(sol_dopri.nfev)
        fe_dopri853.append(sol_dopri853[0].size-1)
        err = 0 
        #return sol_dopri
        for i in range(sol_dopri853[0].size):
            ldt = sol_dopri853[0][i]
            err += ldt * ((sol.y[0,i]-sol_dopri853[1].T[0,i])*(sol.y[0,i]-sol_dopri853[1].T[0,i]) + \
                           (sol.y[1,i]-sol_dopri853[1].T[1,i])*(sol.y[1,i]-sol_dopri853[1].T[1,i])  )
        err = np.sqrt(err)    
        norm_dopri853.append(err)
    
    
    for eps in l_eps:
        vm= vanderpol_model(eps=eps)
        fcn = vm.fcn
        
        sol_dopri =solve_ivp(fcn, (tini, tend), yini, method="RK45", rtol=tol, atol=tol)
        sol = solve_ivp(fcn, (tini, tend), yini, rtol=1.e-13, atol=1.e-13, t_eval=sol_dopri.t)
        #sol_rk_emb.t.size-1
        #fe_dopri.append(sol_dopri.nfev)
        fe_dopri.append(sol_dopri.t.size-1)
        err = 0 
        #return sol_dopri
        for i in range(sol_dopri.t.size):
            ldt = sol_dopri.t[i]
            err += ldt * ((sol.y[0,i]-sol_dopri.y[0,i])*(sol.y[0,i]-sol_dopri.y[0,i]) + \
                           (sol.y[1,i]-sol_dopri.y[1,i])*(sol.y[1,i]-sol_dopri.y[1,i])  )
        err = np.sqrt(err)    
        norm_dopri.append(err)
    #fig = figure(x_axis_type="log", y_axis_type="log", plot_height=500, plot_width=900, title= "Number of function evaluations vs norm of global error"
    #           )
    #fig = figure(x_axis_type="log", y_axis_type="log", plot_height=500, plot_width=900, title= "Number of time steps vs norm of global error" )
    #fig.x(norm_dopri, fe_dopri, legend="DOPRI", color="Indigo")
    #fig.line(norm_dopri, fe_dopri, legend="DOPRI", color="Indigo")
    #fig.x(norm_rk_emb, fe_rk_emb, legend="rk embedded", color="Green")
    #fig.line(norm_rk_emb, fe_rk_emb, legend="rk embedded", color="Green")
    fig = figure(x_axis_type="log", y_axis_type="log", plot_height=500, plot_width=900,
                 title= "accepted time steps vs tolerance")
    fig.x(l_eps, fe_dopri, legend="DOPRI", color="Indigo")
    fig.line(l_eps, fe_dopri, legend="DOPRI", color="Indigo")
    fig.x(l_eps, fe_dopri853, legend="DOPRI853", color="red")
    fig.line(l_eps, fe_dopri853, legend="DOPRI853", color="red")
    #fig.x(l_tol, fe_dopri853, legend="DOPRI853", color="red")
    #fig.line(l_tol, fe_dopri853, legend="DOPRI853", color="red")
    fig.legend.location = "top_left"
    show(fig)
    
a=plot_embedded_cost()